## A demo using Hydrogen Hamiltonian with GPT-QE.

In [2]:
import torch



In [3]:
from qwrapper.operator import PauliObservable
from gqe.mingpt.cost import EnergyCost
from qswift.compiler import DefaultOperatorPool
from benchmark.molecule import DiatomicMolecularHamiltonian
from gqe.operator_pool.uccsd import UCCSD, generate_molecule
from gqe.common.initializer import HFStateInitializer
from gqe.util import get_device
from gqe.mingpt.callback import DefaultCallback, PrintMonitor, FileMonitor
import logging

logging.getLogger('benchmark.molecule').setLevel(logging.WARNING)

# molecule = generate_molecule("Li", "H", 1.596, "sto-3g", bravyi_kitaev=False)
molecule = generate_molecule("N", "N", 2.0, "sto-3g", active_orbitals=[4, 5, 6, 7, 8, 9],
                             bravyi_kitaev=False)
nqubit = 12

# prepare Hamiltonian
hamiltonian = DiatomicMolecularHamiltonian(nqubit, molecule, bravyi_kitaev=False)

# prepare operator_pool
uccsd = UCCSD(nqubit, molecule)
paulis = uccsd.paulis
paulis.append(PauliObservable("IIIIIIIIIIII"))
print('paulis', paulis)
num_operators = len(paulis)
initializer = HFStateInitializer(n_electrons=6)
pool = DefaultOperatorPool(paulis)
cost = EnergyCost(hamiltonian, initializer, pool,
                  [0.00625, -0.00625, 0.0125, -0.0125, 0.025, -0.025, 0.05, -0.05, 0.1, -0.1, 0.2, -0.2],
                  tool='qulacs')


converged SCF energy = -106.871504045608
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped

## FCI energy by diagonalization

In [38]:
from qwrapper.hamiltonian import compute_ground_state

# print(compute_ground_state(hamiltonian))
print('-107.43702368448199')

-107.43702368448199


In [39]:
print("hf state:", hamiltonian.exact_value(initializer.init_circuit(12, [], "qulacs")))

hf state: -106.8715040456087


## Setup for GPT

In [40]:
# create a GPT instance
from gqe.mingpt.model import GPT


def get_gpt():
    model_config = GPT.get_default_config()
    model_config.model_type = 'gpt2'
    model_config.vocab_size = cost.vocab_size()
    model_config.n_gates = 45  # The number of gates for each circuit
    model_config.block_size = model_config.n_gates
    model_config.temperature = 5  # Each gate is generated with probability exp(-temperature * logit)
    model_config.embd_pdrop = 0
    model_config.resid_pdrop = 0
    model_config.attn_pdrop = 0
    model_config.std = 0.02
    model_config.energy_offset = 106
    model = GPT(model_config, cost)
    return model

In [41]:
# create a Trainer object
from gqe.mingpt.trainer import Trainer


def get_trainer(model):
    train_config = Trainer.get_default_config()
    train_config.learning_rate = 5e-7  # the model we're using is so small that we can go a bit faster
    train_config.max_iters = 500
    train_config.num_workers = 10
    train_config.n_samples = 50
    trainer = Trainer(train_config, model)
    return trainer

In [43]:
energies = []
for j in range(10, 20):
    model = get_gpt()
    trainer = get_trainer(model)
    file_monitor = FileMonitor()
    callback_generator = DefaultCallback(model, monitors=[PrintMonitor(), file_monitor])
    trainer.set_callback('on_batch_end', callback_generator.generate())
    trainer.run()
    torch.save(model.state_dict(), f'../saved_models/gptqe_test_nytrogen_{j}')
    file_monitor.save(f'../output/trajectory_test_nytrogen_{j}')
    energies.append(file_monitor.min_energy)
for e in energies:
    print(e)

number of parameters: 86.37M
running on device mps
iter_dt 0.00s; iter 0: train loss 2.88977 temperature: 5
mean_logits tensor([-107.3898, -107.3549, -107.4165, -107.4553, -107.4666, -107.3358,
        -107.3863, -107.3453, -107.3605, -107.3886, -107.3651, -107.4775,
        -107.3632, -107.3930, -107.4555, -107.5031, -107.4257, -107.3947,
        -107.4238, -107.4743, -107.4956, -107.3765, -107.4000, -107.3222,
        -107.4899, -107.5044, -107.4275, -107.3068, -107.5488, -107.4975,
        -107.4011, -107.4236, -107.3512, -107.4344, -107.4491, -107.4692,
        -107.1936, -107.4906, -107.3723, -107.4254, -107.4208, -107.2904,
        -107.5439, -107.3705, -107.3919, -107.5017, -107.4924, -107.4239,
        -107.2507, -107.2429], device='mps:0', grad_fn=<SubBackward0>)
energies: tensor([-106.8632, -106.8972, -106.9523, -106.9137, -106.9752, -106.8587,
        -106.9159, -106.9661, -106.9130, -106.7979, -106.9182, -106.8195,
        -106.9088, -107.0094, -106.8243, -106.5030, -106.99

In [19]:
from gqe.mingpt.data import EnergyDataset

data = EnergyDataset(['../output/trajectory_test_nytrogen_19'])
# cost.sequence.tool = "qiskit"
# indices = file_monitor.min_indices
# cost.sequence._get_circuit(indices).qc.draw(output="mpl", plot_barriers=True)

In [20]:
from gqe.util import to_pqc, to_time_evolutions
from gqe.vqa.initializer import InitializerDelegate
from qwrapper.optimizer import AdamOptimizer
from qml.core.vqe import VQE
from qml.core.pqc import TimeEvolutionPQC
from qml.core.function import Energy

pqc = TimeEvolutionPQC(cost.sequence.observable.nqubit)
evolutions = to_time_evolutions(cost.sequence, data.min_indices)
for evolution in evolutions:
    pqc.add_time_evolution(evolution.pauli, evolution.t)
initializer = InitializerDelegate(HFStateInitializer(n_electrons=6), nqubit, "qulacs")
optimizer = AdamOptimizer(maxiter=3000)

energy = Energy(hamiltonian, nqubit, pqc)
vqe = VQE(energy, initializer, optimizer)
print(vqe.value())
vqe.exec()
print(vqe.value())


-107.40624975383788
0 -107.40624975383788
1 -107.40698920597315
2 -107.40756596521709
3 -107.40798447184562
4 -107.40834893148737
5 -107.40872777917944
6 -107.40911949379287
7 -107.40951161030092
8 -107.40989829445705
9 -107.41026598399476
10 -107.41060079757756
11 -107.41090367048783
12 -107.41118462309014
13 -107.41145100021063
14 -107.41170770323178
15 -107.41196104756257
16 -107.41221696491391
17 -107.412475369505
18 -107.41273178508752
19 -107.4129841051357
20 -107.41323380967917
21 -107.41348218807002
22 -107.41372947680925
23 -107.41397700190238
24 -107.4142271436854
25 -107.41448023982565
26 -107.41473375204822
27 -107.414985085414
28 -107.41523300645531
29 -107.4154763316105
30 -107.4157137041002
31 -107.41594513102123
32 -107.41617210831441
33 -107.41639570567897
34 -107.4166158441553
35 -107.41683246658808
36 -107.41704581767574
37 -107.41725565528981
38 -107.41746157307648
39 -107.41766399503155
40 -107.4178638555116
41 -107.41806158499568
42 -107.41825722469098
43 -107.418

KeyboardInterrupt: 